# EEZYbotARM MK3 - Denavit-Hartenberg DK

## Trabajo Práctico Róbotica
* **Profesor:** Ing. Hugo Pailos
* **Alumnos:**
    - Gerardo Collante
    - Nicolás Quinteros Castilla

## TODO
- [x] Write the press release
- [ ] Update the website
- [ ] Contact the media 

![Image of Yaktocat](EEZYBOTarmMK3.png "Robot EEZYbotARM MK3")

In [11]:
import sympy as sp
import matplotlib.pyplot as plt
import numpy as np
import plotly.graph_objects as go

%matplotlib inline
from numpy import *
d2r = np.deg2rad
r2d = np.degrees

In [12]:
from sympy.physics.vector import init_vprinting
init_vprinting(use_latex='mathjax', pretty_print=False)

In [13]:
from sympy.physics.mechanics import dynamicsymbols

### Parámetros DH

In [14]:
theta, alpha, a, d = dynamicsymbols('theta alpha a d')
theta, alpha, a, d 

(theta, alpha, a, d)

In [15]:
rot = sp.Matrix([[sp.cos(theta), -sp.sin(theta)*sp.cos(alpha), sp.sin(theta)*sp.sin(alpha)],
                 [sp.sin(theta), sp.cos(theta)*sp.cos(alpha), -sp.cos(theta)*sp.sin(alpha)],
                 [0, sp.sin(alpha), sp.cos(alpha)]])

trans = sp.Matrix([a*sp.cos(theta),a*sp.sin(theta),d])

last_row = sp.Matrix([[0, 0, 0, 1]])

m = sp.Matrix.vstack(sp.Matrix.hstack(rot, trans), last_row)
m

Matrix([
[cos(theta), -sin(theta)*cos(alpha),  sin(alpha)*sin(theta), a*cos(theta)],
[sin(theta),  cos(alpha)*cos(theta), -sin(alpha)*cos(theta), a*sin(theta)],
[         0,             sin(alpha),             cos(alpha),            d],
[         0,                      0,                      0,            1]])

### Parámetros del robot

In [16]:
theta1, theta2, theta3 = dynamicsymbols('theta1 theta2 theta3')
theta1, theta2, theta3

(theta1, theta2, theta3)

### Tabla DH

| $i$ | $\theta_i$                  | $d_i$ | $a_i$ | $\alpha_i$      |
|-:-:-|-:-:-------------------------|-:-:---|-:-:---|-:-:-------------|
| 1   | $\theta_1^*$                | $d_1$ | 0     | $\frac{\pi}{2}$ |
| 2   | $\frac{\pi}{2}+\theta_2^*$  | 0     | $a_2$ | 0               |
| 3   | $\frac{-\pi}{2}+\theta_3^*$ | 0     | $a_3$ | 0               |
| 4   | $\frac{\pi}{2} $            | 0     | 0     | $\frac{\pi}{2}$ |

$-30° \leq \theta_1 \leq 30° ; -36° \leq \theta_2 \leq 56°; -44° \leq \theta_3 \leq 0°$

$i$: número del enlace, $\alpha_i$: ángulo de torsión, $a_i$: longitud del enlace $i$, $d_i$: offset de la articulación y $\theta_i$: ángulo de articulación. 

In [17]:
# Link lenghts [m]
#d1 = 0.034
d1 = 0.07
a2 = 0.08
a3 = 0.14

# Compute DH-matrix
m01 = m.subs({theta:theta1, d:d1, a:0, alpha:pi/2})
m12 = m.subs({theta:pi/2+theta2, d:0, a:a2, alpha:0})
m23 = m.subs({theta:-pi/2+theta3, d:0, a:a3, alpha:0})
m34 = m.subs({theta:pi/2, d:0, a:0, alpha:pi/2})
m04 = (m01*m12*m23*m34)

mtcp = sp.simplify(m04)

# Create function
px = mtcp[0,3]
py = mtcp[1,3]
pz = mtcp[2,3]
fx = sp.lambdify((theta1, theta2, theta3), px, 'numpy')
fy = sp.lambdify((theta1, theta2, theta3), py, 'numpy')
fz = sp.lambdify((theta1, theta2, theta3), pz, 'numpy')

In [18]:
mtcp[:,3]

Matrix([
[-8.57252759403147e-18*sin(theta2 + theta3)*sin(theta1) - 2.99951956532372e-34*sin(theta1)*sin(theta2) - 4.89858719658941e-18*sin(theta1)*cos(theta2) - 0.08*sin(theta2)*cos(theta1) + 0.14*cos(theta2 + theta3)*cos(theta1) + 4.89858719658941e-18*cos(theta1)*cos(theta2)],
[ 8.57252759403147e-18*sin(theta2 + theta3)*cos(theta1) - 0.08*sin(theta1)*sin(theta2) + 0.14*sin(theta1)*cos(theta2 + theta3) + 4.89858719658941e-18*sin(theta1)*cos(theta2) + 2.99951956532372e-34*sin(theta2)*cos(theta1) + 4.89858719658941e-18*cos(theta1)*cos(theta2)],
[                                                                                                                                                                                   0.14*sin(theta2 + theta3) + 4.89858719658941e-18*sin(theta2) + 0.08*cos(theta2) + 0.034],
[                                                                                                                                                                                    

$$p_{tcp} = 
\begin{bmatrix}
-a_2 \cdot \cos(\theta_1) \cdot \sin(\theta_2) +a_3 \cdot \cos (\theta_1) \cdot \cos(\theta_2 + \theta_3)\\
−a_2 \cdot \sin(\theta_1)\cdot \sin(\theta_2)+ a_3 \cdot \sin(\theta_1) \cdot \cos(\theta_2+\theta_3) \\
a_2 \cdot \cos(\theta_2) + a_3 \cdot \sin (\theta_2 + \theta_3) + d_1
\end{bmatrix}$$

$$ p_x = -a_2 \cdot \cos(\theta_1) \cdot \sin(\theta_2) +a_3 \cdot \cos (\theta_1) \cdot \cos(\theta_2 + \theta_3) $$

$$ p_y =  −a_2 \cdot \sin(\theta_1)\cdot \sin(\theta_2)+ a_3 \cdot \sin(\theta_1) \cdot \cos(\theta_2+\theta_3) $$


$$ p_z = a_2 \cdot \cos(\theta_2) + a_3 \cdot \sin (\theta_2 + \theta_3) + d_1 $$

In [19]:
'''
px = -a2*sp.cos(theta1)*sp.sin(theta2) + a3 * sp.cos(theta1) * sp.cos(theta2 + theta3)
py = -a2*sp.sin(theta1)*sp.sin(theta2) + a3 * sp.sin(theta1) * sp.cos(theta2 + theta3)
pz = a2*sp.cos(theta2) + a3 * sp.sin(theta1+theta2) + d1
fx = sp.lambdify((theta1, theta2, theta3), px, 'numpy')
fy = sp.lambdify((theta1, theta2, theta3), py, 'numpy')
fz = sp.lambdify((theta1, theta2, theta3), pz, 'numpy')
'''

"\npx = -a2*sp.cos(theta1)*sp.sin(theta2) + a3 * sp.cos(theta1) * sp.cos(theta2 + theta3)\npy = -a2*sp.sin(theta1)*sp.sin(theta2) + a3 * sp.sin(theta1) * sp.cos(theta2 + theta3)\npz = a2*sp.cos(theta2) + a3 * sp.sin(theta1+theta2) + d1\nfx = sp.lambdify((theta1, theta2, theta3), px, 'numpy')\nfy = sp.lambdify((theta1, theta2, theta3), py, 'numpy')\nfz = sp.lambdify((theta1, theta2, theta3), pz, 'numpy')\n"

### Ploteo del área del trabajo del robot

In [22]:
n_theta = 36

theta1s = np.linspace(d2r(-30), d2r(30), n_theta) # desired range of motion for joint 1
theta2s = np.linspace(d2r(-36), d2r(56), n_theta) # desired range of motion for joint 2
theta3s = np.linspace(d2r(-44), d2r(0), n_theta) # desired range of motion for joint 3

total = len(theta1s)*len(theta2s)*len(theta3s)
print(total)

posx = []
posy = []
posz = []

counter = 0

for t1 in theta1s:
    for t2 in theta2s:
        for t3 in theta3s:
            x = float(fx(t1, t2, t3))
            y = float(fy(t1, t2, t3))
            z = float(fz(t1, t2, t3))
            posx.append(x)
            posy.append(y)
            posz.append(z)
#                 y = fy(l1,l2,theta1,theta2)
x = np.array(posx)
y = np.array(posy)
z = np.array(posz)

'''
fig = go.Figure(data=go.Scatter3d(
    x=x, y=y, z=z,
    marker=dict(
        size=4,
        color=z,
        colorscale='Viridis',
    ),
    line=dict(
        color='darkblue',
        width=2
    )
))

'''
data = go.Scatter3d(
    x=x, 
    y=y, 
    z=z,
    mode='markers', 
    opacity=0.025,  
    marker=dict(
        size=4,
        color=z,
        colorscale='Viridis',
        line=dict(
            color='rgb(0, 0, 0)',
            width=1
        )
    ))

layout = go.Layout(
    scene = go.layout.Scene(
    aspectmode='manual',
    aspectratio=go.layout.scene.Aspectratio(
        x=1, y=1, z=1
    ))
)

fig = go.Figure(data=data, layout=layout)

fig.add_trace(go.Scatter3d(
     x=[0,0.0], 
     y=[0,0.0], 
     z=[0,0.1],
     marker=dict(
         symbol='diamond',
         size=5,
         color='rgb(0,0,0)'
     ),
     line=dict(
        color='blue',
        width=3
    )))

fig.add_trace(go.Scatter3d(
     x=[0,0.0], 
     y=[0,0.1], 
     z=[0,0.0],
     marker=dict(
         symbol='diamond',
         size=5,
         color='rgb(0,0,0)'
     ),
     line=dict(
        color='green',
        width=3
    )))

fig.add_trace(go.Scatter3d(
     x=[0,0.1], 
     y=[0,0.0], 
     z=[0,0.0],
     marker=dict(
         symbol='diamond',
         size=5,
         color='rgb(0,0,0)'
     ),
     line=dict(
        color='red',
        width=3
    )))

'''
fig.add_trace(go.Scatter3d(
     x=[x_target], 
     y=[y_target], 
     z=[z_target],
     mode='markers', 
     marker=dict(
         symbol='x',
         size=5,
         color='rgb(255,255,255)'
     )))
'''

fig.show()

46656


In [ ]:
target_param = [d2r(35.0), d2r(36.0), d2r(-10)]
target = f(target_param)
#target = np.array([0.18, 0.016, 0.15])
x_target = target[0]
y_target = target[1]
z_target = target[2]
print(target)
# Obtener punto valuando los parámetros

In [ ]:
# Function
def f(param):
    p0 = param[0]
    p1 = param[1]
    p2 = param[2]
    
    point = []
    point = ([fx(p0, p1, p2),
              fy(p0, p1, p2),
              fz(p0, p1, p2)])
    
    return np.array(point)

# Distancia euclidiana
def distance(p1, p2):
    dist = np.linalg.norm(p1-p2)
    return dist

## IK mediante por barrido aleatorio de fuerza bruta

In [ ]:
%%time

n_theta = 36
d_n = 20

params = []

theta1s = np.linspace(d2r(-30), d2r(30), n_theta) # desired range of motion for joint 1
theta2s = np.linspace(d2r(-36), d2r(56), n_theta) # desired range of motion for joint 2
theta3s = np.linspace(d2r(-60), d2r(60), n_theta) # desired range of motion for joint 3

for theta1 in theta1s:
        for theta2 in theta2s:
            for theta3 in theta3s:
                params.append([theta1, theta2, theta3])

params = np.array(params)
np.random.shuffle(params)

actual_err = 100
required_err = 0.01

counter = 0

points = []

for param in params:
    points.append(f(param))
    new_err = distance(f(param), target)
    counter += 1
    if new_err<actual_err:
        actual_err = new_err
        best_param = param
    if new_err<required_err:
        break

In [ ]:
# Setear mejores puntos para el ploteo
best = f(best_param)
x_best = best[0]
y_best = best[1]
z_best = best[2]

points = np.array(points)

print(counter)
print('error actual:', actual_err)
print('parametros:', r2d(best_param))
print('target:', target)
print('achieved:', f(best_param))